In [46]:
import gym
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
import math
import random

In [18]:
env = gym.make('CartPole-v1')

num_actions = env.action_space.n
state_space_dimensions = env.observation_space.shape[0]

print('Actions: {} -- State space dimensions: {}'.format(num_actions, state_space_dimensions))

Actions: 2 -- State space dimensions: 4


/home/alessandro/projects/uni/autonomous/.venv/lib64/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [163]:
class CartPoleDQN(nn.Module):
    
    def __init__(self):
        super(CartPoleDQN, self).__init__()
        self.fc1 = nn.Linear(state_space_dimensions, 256)
        self.fc2 = nn.Linear(256, 64)
        #self.fc3 = nn.Linear(128, 64)
        self.head = nn.Linear(64, num_actions)
    
    def forward(self, x):
        x = F.leaky_relu(self.fc1(x))
        x = F.leaky_relu(self.fc2(x))
        #x = F.leaky_relu(self.fc3(x))
        x = F.leaky_relu(self.head(x))
        return x

In [213]:
class ReplayBuffer():
    
    def __init__(self, capacity):
        self.capacity = capacity
        self.position = 0
        self.states = []
        self.actions = []
        self.rewards = []
        self.next_states = []
        self.done = []
        
        
    def push(self, state, action, reward, next_state, done):
        if len(self.states) < self.capacity:
            self.states.append(None)
            self.actions.append(None)
            self.rewards.append(None)
            self.next_states.append(None)
            self.done.append(None)
            
        self.states[self.position] = state
        self.actions[self.position] = action
        self.rewards[self.position] = reward
        self.next_states[self.position] = next_state
        self.done[self.position] = done
        
        self.position = (self.position + 1) % self.capacity
        
        
    def sample(self, batch_size):
        indices = np.random.choice(range(len(self.states)), size=batch_size)
        state_sample = [self.states[i] for i in indices]
        action_sample = [self.actions[i] for i in indices]
        reward_sample = [self.rewards[i] for i in indices]
        next_state_sample = [self.next_states[i] for i in indices]
        done_sample = [self.done[i] for i in indices]
        
        return state_sample, action_sample, reward_sample, next_state_sample, done_sample
        
    def __len__(self):
        return len(self.states)

In [214]:
def select_action(state, env, model, epsilon):
    if random.random() > epsilon:
        with torch.no_grad():
            return model(state).argmax().item()
    else:
        return env.action_space.sample()
    

In [215]:
def update_epsilon(epsilon_start, epsilon_end, epsilon_steps, total_steps):
    return epsilon_end + (epsilon_start - epsilon_end) * math.exp(-1. * total_steps / epsilon_steps)  
    

In [239]:
def optimize_model(policy_net, target_net, optimizer, memory, batch_size, gamma):
    state_batch, action_batch, reward_batch, next_state_batch, done_batch = memory.sample(batch_size)
        
    state_batch = torch.tensor(state_batch).float().view((batch_size, -1))
    action_batch = torch.tensor(action_batch, dtype=torch.int64).view((batch_size))
    reward_batch = torch.tensor(reward_batch).float().view((batch_size))
    
    non_final_next_states = torch.tensor([s for s in next_state_batch if s is not None]).float()
    non_final_mask = torch.tensor(list(map(lambda s: s is not None, next_state_batch)), dtype=torch.bool)
        
    state_action_values = policy_net(state_batch)
    state_action_values = state_action_values.gather(1, action_batch.reshape((batch_size, 1)))
    
    next_state_values = torch.zeros(batch_size)
    next_state_values[non_final_mask] = target_net(non_final_next_states).max(dim=1)[0].float().detach()
        
    expected_state_action_values = reward_batch + gamma * next_state_values
    
    loss = F.smooth_l1_loss(state_action_values, expected_state_action_values.unsqueeze(1))
    
    optimizer.zero_grad()
    loss.backward()
    optimizer.step()
    
    return loss
    
    

def train_dqn(env, policy_net, target_net, optimizer, memory, target_update=10, batch_size=32, episodes=100, gamma=0.99, epsilon_start=0.9, epsilon_end=0.05, epsilon_steps=1000000):
    
    total_rewards = []
    total_steps = 0
    
    epsilon = epsilon_start
        
    for episode in range(episodes):
        
        done = False
        state = env.reset()
        
        total_rewards.append(0)
        loss = 0
        
        while not done:
            
            env.render()
            state_tensor = torch.tensor(state).float()
            action = select_action(state_tensor, env, policy_net, epsilon)
            
            next_state, reward, done, _ = env.step(action)
            
            if done:
                next_state = None
            
            total_rewards[episode] += reward
            
            
            memory.push(state, action, reward, next_state, done)
            
            
            state = next_state
            
            if len(memory) >= batch_size:                 
                loss = optimize_model(policy_net, target_net, optimizer, memory, batch_size, gamma)
        
            if total_steps % target_update == 0:
                target_net.load_state_dict(policy_net.state_dict())
                
            total_steps += 1
            epsilon = update_epsilon(epsilon_start, epsilon_end, epsilon_steps, total_steps)
            
        
        print('{}/{} Total steps: {} Episode reward: {} Average reward: {} Loss: {} Epsilon: {}'.format(episode, episodes, total_steps, total_rewards[episode], np.mean(total_rewards), loss, epsilon))

            
                   

In [238]:
env = gym.make('CartPole-v1')

num_actions = env.action_space.n
state_space_dimensions = env.observation_space.shape[0]

target_net = CartPoleDQN()
policy_net = CartPoleDQN()

#policy_net.load_state_dict(target_net.state_dict())

optimizer = torch.optim.Adam(policy_net.parameters())

memory = ReplayBuffer(100000)
try:
    train_dqn(env, policy_net, target_net, optimizer, memory, gamma=0.5, batch_size=128, episodes=1000, epsilon_steps=10000)
finally:
    env.close()

0/1000 Total steps: 74 Episode reward: 74.0 Average reward: 74.0 Loss: 0 Epsilon: 0.8937332156993122
1/1000 Total steps: 92 Episode reward: 18.0 Average reward: 46.0 Loss: 0 Epsilon: 0.8922158619391231
2/1000 Total steps: 109 Episode reward: 17.0 Average reward: 36.333333333333336 Loss: 0 Epsilon: 0.8907853112864057
3/1000 Total steps: 122 Episode reward: 13.0 Average reward: 30.5 Loss: 0 Epsilon: 0.8896930005375538
tensor([1.0277, 1.0312, 1.0496, 1.0114, 1.0352, 1.0181, 1.0492, 1.0375, 1.0217,
        1.0058, 1.0444, 1.0538, 1.0090, 1.0331, 1.0067, 1.0417, 1.0510, 1.0496,
        1.0448, 1.0277, 1.0538, 1.0251, 1.0270, 1.0107, 1.0183, 1.0325, 1.0497,
        1.0087, 1.0317, 1.0283, 1.0317, 1.0348, 1.0206, 1.0261, 1.0417, 1.0434,
        1.0405, 1.0315, 1.0251, 1.0496, 1.0538, 1.0405, 1.0343, 1.0560, 1.0299,
        1.0292, 1.0537, 1.0044, 1.0267, 1.0278, 1.0115, 1.0270, 1.0293, 1.0240,
        1.0277, 1.0299, 1.0375, 1.0267, 1.0496, 1.0121, 1.0496, 1.0312, 1.0434,
        1.0317, 1.03

tensor([1.1678, 1.2590, 1.1718, 1.2693, 1.2227, 1.1842, 1.2995, 1.1977, 1.2837,
        1.3164, 1.3362, 1.1862, 1.2709, 1.2320, 1.2046, 1.2221, 1.2971, 1.2327,
        1.2590, 1.0000, 1.1702, 1.1963, 1.1807, 1.1720, 1.1807, 1.1865, 1.2248,
        1.2145, 1.1741, 1.2990, 1.2221, 1.3081, 1.2220, 1.3105, 1.1807, 1.1865,
        1.1702, 1.2294, 1.1902, 1.2709, 1.2709, 1.1728, 1.2212, 1.1912, 1.1977,
        1.2395, 1.2675, 1.1720, 1.2235, 1.1915, 1.1842, 1.2333, 1.1699, 1.2007,
        1.2212, 1.2642, 1.1916, 1.2438, 1.1678, 1.2917, 1.2675, 1.2746, 1.1977,
        1.1741, 1.2235, 1.2210, 1.2675, 1.3081, 1.3362, 1.2746, 1.1720, 1.2981,
        1.1912, 1.1956, 1.1915, 1.2294, 1.0000, 1.3872, 1.2235, 1.2707, 1.1728,
        1.2248, 1.2271, 1.3344, 1.2707, 1.2221, 1.2294, 1.1678, 1.1735, 1.2709,
        1.2395, 1.1728, 1.1807, 1.2235, 1.1915, 1.2333, 1.3872, 1.2325, 1.1684,
        1.1920, 1.2145, 1.1723, 1.3105, 1.1923, 1.2812, 1.1865, 1.1974, 1.2725,
        1.2133, 1.1981, 1.1673, 1.3449, 

tensor([1.6175, 1.7772, 1.0000, 1.5408, 1.6905, 1.7188, 1.5193, 1.5756, 1.7795,
        1.5491, 1.0000, 1.5144, 1.5410, 1.0000, 1.5293, 1.7369, 1.6527, 1.5156,
        1.5583, 1.7077, 1.6874, 1.5992, 1.8923, 1.5425, 1.9080, 1.5454, 1.5676,
        1.5505, 1.8048, 1.5327, 1.5319, 1.6808, 1.5478, 1.9080, 1.6221, 1.0000,
        1.5152, 1.6805, 1.5349, 1.6123, 1.5410, 1.5284, 1.6162, 1.5569, 1.5992,
        1.7188, 1.5703, 1.5425, 1.6451, 1.5410, 1.5243, 1.5493, 1.5505, 1.5954,
        1.7461, 2.0122, 1.6162, 1.7461, 1.5170, 1.5319, 1.6670, 1.7772, 1.9080,
        1.7809, 1.5676, 1.6303, 1.5964, 1.5676, 1.5978, 1.5185, 1.7694, 1.7772,
        1.5408, 1.5569, 1.0000, 1.6008, 1.5765, 1.6451, 1.8295, 1.7694, 1.5569,
        1.6773, 1.8418, 1.5484, 1.5403, 1.5225, 1.5477, 1.5403, 1.5185, 1.7772,
        1.5349, 1.6009, 1.5284, 1.8465, 1.7648, 1.5676, 1.6583, 1.6162, 1.5401,
        2.1786, 1.5178, 1.6583, 1.5225, 1.5966, 1.6583, 1.7477, 1.9231, 1.9080,
        1.6808, 1.7477, 1.5676, 1.5658, 

tensor([1.8970, 1.8058, 1.9499, 1.0000, 1.9999, 2.0475, 1.8199, 2.4497, 1.8292,
        1.8437, 1.8284, 1.9125, 1.9986, 1.8366, 2.1972, 2.0383, 1.8532, 2.0987,
        2.2803, 1.8292, 1.8374, 1.0000, 1.8199, 1.9335, 2.2337, 1.9999, 1.8366,
        1.8817, 1.9413, 2.1331, 2.1194, 1.8129, 1.8354, 1.8392, 1.8394, 2.0136,
        1.8205, 1.8225, 2.0011, 1.8058, 1.8073, 2.1324, 1.0000, 1.8351, 2.0099,
        2.1764, 2.3090, 2.4575, 2.0585, 2.1751, 1.9880, 1.9335, 1.8114, 2.1177,
        2.1764, 1.8366, 1.8970, 1.8237, 1.8599, 2.0001, 1.9172, 1.8349, 1.8197,
        2.0585, 1.9124, 1.8374, 2.1177, 1.9936, 1.8349, 1.9212, 1.8437, 2.3234,
        1.9254, 1.9202, 1.0000, 2.0069, 1.8599, 1.8679, 1.8679, 1.8354, 2.0069,
        2.1693, 1.8423, 1.9132, 1.8225, 2.1764, 1.8423, 1.8366, 1.8532, 2.1054,
        1.8970, 2.6659, 1.9125, 1.8421, 2.0022, 1.8351, 1.8311, 1.8073, 1.0000,
        1.8303, 1.0000, 1.8421, 1.8423, 1.9140, 2.0028, 2.2458, 2.0738, 2.2337,
        2.0383, 1.9202, 2.1159, 2.0097, 

tensor([1.9327, 1.9498, 2.0032, 2.0097, 2.0526, 1.9581, 1.9405, 2.0874, 1.9645,
        2.0526, 2.0427, 2.0115, 1.0000, 1.9368, 2.0526, 2.2596, 1.9618, 2.1560,
        2.0711, 1.0000, 2.3135, 1.9378, 2.2963, 1.9370, 1.9368, 1.9724, 2.0661,
        2.0511, 2.0706, 2.0261, 1.0000, 2.0711, 2.1097, 2.0884, 1.9511, 1.9645,
        1.9756, 2.0909, 2.0127, 1.9816, 1.9326, 2.1007, 2.0127, 2.2576, 2.0009,
        2.0548, 1.0000, 1.9605, 1.9581, 1.0000, 2.0013, 1.9585, 2.0520, 2.3692,
        2.0793, 1.9954, 2.0123, 2.0520, 1.9646, 2.1064, 2.0615, 1.9646, 2.1231,
        1.9657, 2.0793, 2.1759, 1.9615, 2.0765, 1.9821, 1.9683, 2.1699, 1.9706,
        2.1783, 1.9458, 2.0854, 2.0123, 1.9621, 1.9416, 1.9945, 1.9976, 1.9611,
        2.3135, 1.0000, 2.1031, 2.1016, 2.0014, 1.9326, 1.9621, 1.9581, 1.9621,
        2.0520, 2.1225, 1.9646, 1.9467, 1.9704, 2.0032, 2.0279, 2.0639, 2.0661,
        1.9657, 2.0604, 1.9523, 2.1118, 1.9283, 1.9718, 2.0261, 1.9368, 2.2576,
        1.9283, 1.9576, 2.0792, 1.9405, 

...

tensor([2.0399, 1.0000, 2.0184, 2.0102, 2.0120, 2.0423, 2.0181, 2.0302, 2.0382,
        2.0234, 2.0130, 2.0162, 2.0194, 2.0150, 1.8499, 2.0207, 2.0255, 2.0189,
        2.0261, 2.0283, 2.0202, 2.0106, 2.0122, 2.0401, 2.0134, 2.0174, 2.0099,
        1.9950, 1.9788, 1.9719, 2.0164, 2.0239, 2.0136, 2.0211, 2.0159, 2.0311,
        2.0215, 2.0182, 2.0227, 2.0154, 2.0177, 2.0077, 2.0151, 2.0195, 1.7240,
        2.0244, 1.0000, 1.9958, 1.8690, 2.0235, 2.0142, 2.0172, 2.0262, 2.0199,
        1.0000, 2.0287, 1.7673, 2.0182, 1.6558, 2.0076, 2.0174, 2.0304, 2.0119,
        2.0056, 2.0189, 2.0129, 2.0462, 2.0204, 2.0187, 1.0000, 1.9870, 1.9226,
        2.0216, 2.0284, 2.0239, 2.0247, 2.0609, 1.6274, 2.0427, 1.5630, 2.0459,
        1.0000, 2.0182, 2.0205, 2.0169, 2.0229, 1.9928, 2.0268, 2.0157, 2.0385,
        1.9413, 2.0189, 2.0079, 2.0254, 1.5838, 2.0218, 1.7911, 2.0200, 2.0332,
        2.0230, 2.0005, 2.0166, 2.0246, 2.0207, 2.0372, 1.9925, 2.0203, 2.0016,
        2.0310, 2.0169, 2.0217, 2.0227, 

tensor([2.0187, 2.0669, 2.0072, 2.0204, 1.7958, 1.9880, 2.0175, 2.0259, 1.9869,
        2.0168, 2.0101, 2.0147, 2.0090, 2.0154, 2.0227, 2.0374, 2.0069, 2.0137,
        2.0285, 1.9817, 2.0234, 2.0276, 2.0115, 1.5571, 2.0121, 2.0122, 1.4671,
        2.0005, 1.8331, 2.0170, 2.0121, 2.0387, 1.9986, 2.0225, 2.0136, 2.0112,
        2.0168, 2.0247, 1.9960, 2.0545, 2.0438, 2.0081, 2.0353, 2.0191, 2.0544,
        2.0267, 2.0160, 2.0156, 2.0340, 2.0323, 2.0125, 2.0245, 2.0135, 2.0275,
        2.0135, 2.0181, 2.0074, 1.9518, 2.0204, 2.0056, 1.0000, 2.0113, 1.0000,
        2.0348, 2.0193, 2.0295, 2.0322, 2.0124, 1.9174, 2.0277, 1.7768, 1.0000,
        1.0000, 1.9928, 2.0176, 1.8762, 2.0125, 2.0155, 2.0122, 2.0140, 2.0193,
        2.0180, 2.0600, 2.0236, 2.0166, 2.0398, 2.0140, 2.0156, 2.0098, 1.6417,
        2.0409, 2.0103, 2.0172, 1.0000, 1.5092, 1.9712, 2.0060, 1.9990, 1.8795,
        2.0072, 2.0148, 2.0168, 2.0073, 2.0631, 1.9999, 1.8847, 2.0117, 2.0110,
        2.0194, 1.9645, 2.0222, 2.0163, 

tensor([2.0317, 1.9976, 2.0131, 2.0541, 1.9986, 2.0306, 2.0079, 2.0003, 1.9986,
        1.0000, 1.9991, 2.0145, 2.0179, 1.9918, 2.0162, 1.9986, 1.9918, 1.9470,
        2.0331, 2.0099, 1.0000, 1.0000, 2.0107, 2.0041, 2.0183, 2.0227, 2.0047,
        2.0157, 1.9124, 1.5736, 1.9347, 2.0172, 1.9947, 2.0051, 2.0019, 2.0118,
        2.0078, 1.9940, 2.0081, 2.0159, 2.0203, 1.9848, 2.0033, 2.0038, 2.0079,
        2.0111, 1.9299, 1.9992, 2.0090, 2.0111, 2.0366, 2.0303, 2.0081, 2.0417,
        2.0050, 2.0029, 2.0303, 2.0129, 2.0108, 1.8924, 1.9986, 2.0045, 1.0000,
        1.9972, 2.0108, 2.0297, 2.0051, 2.0096, 1.9923, 2.0154, 2.0027, 2.0198,
        2.0119, 2.0152, 1.9487, 2.0024, 1.5121, 2.0072, 2.0022, 2.0125, 2.0584,
        2.0027, 2.0050, 2.0280, 2.0104, 2.0147, 2.0023, 1.9987, 1.9950, 1.5486,
        2.0299, 2.0001, 1.7861, 2.0113, 2.0139, 2.0091, 1.9421, 2.0187, 2.0007,
        2.0240, 1.5902, 2.0084, 2.0194, 1.9571, 2.0259, 2.0452, 2.0267, 1.9909,
        1.9950, 1.9927, 2.0288, 2.0033, 

tensor([1.9982, 1.9992, 2.0166, 1.9954, 1.8857, 1.9855, 1.9932, 1.9970, 1.9956,
        1.9969, 1.9992, 1.4167, 1.9398, 1.9524, 1.9930, 1.9463, 2.0167, 2.0045,
        2.0047, 2.0003, 2.0116, 1.0000, 2.0184, 1.7119, 1.9955, 1.9990, 1.9962,
        1.9970, 2.0072, 1.9891, 1.9984, 1.9917, 2.0017, 1.9964, 1.5094, 2.0312,
        1.9970, 1.9998, 1.9962, 1.9994, 1.7828, 2.0015, 1.9728, 2.0071, 1.9904,
        1.0000, 1.9855, 1.8832, 2.0012, 2.0169, 2.0424, 1.9940, 2.0012, 1.0000,
        1.9968, 1.9952, 2.0026, 2.0554, 1.9908, 1.9657, 1.9895, 1.9965, 1.9697,
        2.0035, 1.9845, 2.0048, 1.9976, 1.9849, 2.0132, 1.9984, 2.0059, 1.0000,
        2.0072, 1.9935, 1.9659, 2.0049, 1.9969, 2.0117, 1.9729, 1.9958, 2.0052,
        1.9841, 2.0017, 1.9783, 1.9940, 2.0006, 1.9314, 2.0100, 1.9935, 2.0038,
        2.0000, 2.0021, 1.9929, 1.8803, 2.0010, 1.9907, 1.9998, 1.9985, 1.9972,
        2.0050, 2.0018, 2.0032, 2.0034, 2.0034, 2.0181, 1.8667, 2.0009, 1.9907,
        1.8910, 2.0029, 1.9902, 1.9882, 

KeyboardInterrupt: 

In [ ]:
env = gym.make('CartPole-v1')
try:
    train_dqn(env, policy_net, target_net, optimizer, memory, gamma=0.5, batch_size=128, episodes=1000, epsilon_steps=10000)
finally:
    env.close()

0/1000 Total steps: 26 Episode reward: 26.0 Average reward: 26.0 Loss: 0.0006031697848811746 Epsilon: 0.8977928705116843
1/1000 Total steps: 63 Episode reward: 37.0 Average reward: 31.5 Loss: 0.00157302082516253 Epsilon: 0.8946618328823965
2/1000 Total steps: 77 Episode reward: 14.0 Average reward: 25.666666666666668 Loss: 0.0012767084408551455 Epsilon: 0.8934801336988006
3/1000 Total steps: 88 Episode reward: 11.0 Average reward: 22.0 Loss: 0.0006609978736378253 Epsilon: 0.8925528156701522
4/1000 Total steps: 125 Episode reward: 37.0 Average reward: 25.0 Loss: 0.0008753439760766923 Epsilon: 0.8894411304197992
5/1000 Total steps: 149 Episode reward: 24.0 Average reward: 24.833333333333332 Loss: 0.0007136152125895023 Epsilon: 0.8874288873643349
6/1000 Total steps: 181 Episode reward: 32.0 Average reward: 25.857142857142858 Loss: 0.0026661697775125504 Epsilon: 0.8847533979908504
7/1000 Total steps: 193 Episode reward: 12.0 Average reward: 24.125 Loss: 0.0005644232151098549 Epsilon: 0.883